In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Constants
I = np.array([1, 1, 1])  # Moment of inertia
omega = np.array([0.0, 0.0, 2])  # Initial angular velocity
theta = np.array([0.0, 0.0, 0.0])  # Initial angle
Bactual = np.array([1500, 0, 0]) * 10e-6
X_contribution = np.array([30000, 2000, 0]) * 10e-6  # Placeholder for magnetic field contributions
Y_contribution = np.array([2000, 30000, 0]) * 10e-6  # Placeholder for magnetic field contributions
Z_contribution = np.array([0, 0, 10000]) * 10e-6  # Placeholder for magnetic field contributions

stateoftorque = np.array([0, 0.0, 0.0])  # Placeholder for state of torque

Bold = np.array([0.0, 0.0, 0.0])  # Placeholder for Bold
Bdot_old = np.array([0.0, 0.0, 0.0])  # Placeholder for BdotOld
steady_state = False  # Placeholder for steady state condition

def torque(t, Bdot):
    global stateoftorque
    stateoftorque = Bdot.copy()   # Update stateoftorque based on Bdot

    M = np.array([0.0, 0.0, 0.0])  # Initialize torque vector
    M += stateoftorque[0] * X_contribution
    M += stateoftorque[1] * Y_contribution
    M += stateoftorque[2] * Z_contribution
    
    # cross product of Bactual and M
    Bactual_vector = np.array(Bactual)
    # Rotate Bactual by theta to get the actual magnetic field vector
    Bactual_vector = np.array([
        Bactual_vector[0] * np.cos(theta[2]) - Bactual_vector[1] * np.sin(theta[2]),
        Bactual_vector[0] * np.sin(theta[2]) + Bactual_vector[1] * np.cos(theta[2]),
        Bactual_vector[2]
    ])
    M_vector = np.array(M)


    
    print(Bactual_vector, M_vector)
    torque_vector = -np.cross(Bactual_vector, M_vector)

    return torque_vector

# Time setup
dt = 0.01
T = 360
time = np.arange(0, T, dt)

# For plotting
theta_history = []
omega_history = []
Bactual_measured_history = []
torque_history = []

# Simulation loop (Euler method)
for t in time:

    # rotate Bactual by theta to get the measured magnetic field
    Bactual_measured = np.array([
        Bactual[0] * np.cos(theta[2]) - Bactual[1] * np.sin(theta[2]),
        Bactual[0] * np.sin(theta[2]) + Bactual[1] * np.cos(theta[2]),
        Bactual[2]
    ])

    M = np.array([0.0, 0.0, 0.0])  # Reset M for each time step
    M += stateoftorque[0] * X_contribution
    M += stateoftorque[1] * Y_contribution
    M += stateoftorque[2] * Z_contribution
    # cross product of Bactual_measured and M
    Bactual_measured = Bactual_measured + M
    print(stateoftorque)

    Bdot = (Bactual_measured - Bold) / dt  # Calculate the rate of change of magnetic field

    K = 1
    if np.linalg.norm(omega) < 1:
        K = round(np.linalg.norm(omega) * 10) /10  # Scale K based on the magnitude of omega
    if np.linalg.norm(omega) < 0.1:
        K = 0.1

    Bdot = np.sign(Bdot) * K
    print("Bdot:", Bdot)
    # Limit Bdot to a maximum value
    tau = torque(t, Bdot)

    omega += (tau / I) * dt
    theta += omega * dt

    Bold = Bactual_measured.copy()  # Update Bold with the measured magnetic field
    Bdot_old = Bdot.copy()  # Update Bdot_old with the current Bdot
    
    theta_history.append(theta.copy())
    omega_history.append(omega.copy())
    Bactual_measured_history.append(Bactual_measured.copy())
    torque_history.append(tau.copy())

print(omega_history)

# average torque over the simulation



# Plot results
plt.figure(figsize=(10, 4))

plt.subplot(1, 2, 1)
plt.plot(time, omega_history)
plt.title('Angular Velocity (ω) vs Time')
plt.xlabel('Time [s]')
plt.ylabel('ω [rad/s]')
plt.grid()

plt.subplot(1, 2, 2)
plt.plot(time, theta_history)
plt.title('Angle (θ) vs Time')
plt.xlabel('Time [s]')
plt.ylabel('θ [rad]')
plt.grid()

plt.tight_layout()
plt.show()

plt.figure(figsize=(10, 4))
plt.plot(time, Bactual_measured_history)
plt.title('Measured Magnetic Field (Bactual_measured) vs Time')
plt.xlabel('Time [s]')
plt.ylabel('Bactual_measured [T]')
plt.grid()
plt.tight_layout()
plt.show()

plt.figure(figsize=(10, 4))
plt.plot(time, torque_history)
plt.plot(time, TorqueIntegrated, 'r--', label='Average Torque')
plt.title('Torque vs Time')
plt.xlabel('Time [s]')
plt.ylabel('Torque [Nm]')
plt.grid()
plt.tight_layout()
plt.show()
# Display final state

plt.figure(figsize=(10, 4))
plt.plot(time, TorqueIntegrated)
plt.title('Integrated Torque vs Time')
plt.xlabel('Time [s]')
plt.ylabel('Integrated Torque [Nm]')
plt.grid()
plt.tight_layout()
plt.show()


[0. 0. 0.]
Bdot: [1. 0. 0.]
[0.015 0.    0.   ] [0.3  0.02 0.  ]
[1. 0. 0.]
Bdot: [1. 1. 0.]
[0.014997   0.00029998 0.        ] [0.32 0.32 0.  ]
[1. 1. 0.]
Bdot: [1. 1. 0.]
[0.014988   0.00059983 0.        ] [0.32 0.32 0.  ]
[1. 1. 0.]
Bdot: [-1.  1.  0.]
[0.01497301 0.00089944 0.        ] [-0.28  0.28  0.  ]
[-1.  1.  0.]
Bdot: [-1. -1.  0.]
[0.01495203 0.00119868 0.        ] [-0.32 -0.32  0.  ]
[-1. -1.  0.]
Bdot: [-1. -1.  0.]
[0.01492507 0.00149744 0.        ] [-0.32 -0.32  0.  ]
[-1. -1.  0.]
Bdot: [-1.  1.  0.]
[0.01489214 0.00179562 0.        ] [-0.28  0.28  0.  ]
[-1.  1.  0.]
Bdot: [1. 1. 0.]
[0.01485325 0.00209307 0.        ] [0.32 0.32 0.  ]
[1. 1. 0.]
Bdot: [1. 1. 0.]
[0.01480843 0.00238967 0.        ] [0.32 0.32 0.  ]
[1. 1. 0.]
Bdot: [-1.  1.  0.]
[0.01475768 0.00268532 0.        ] [-0.28  0.28  0.  ]
[-1.  1.  0.]
Bdot: [-1. -1.  0.]
[0.01470103 0.00297988 0.        ] [-0.32 -0.32  0.  ]
[-1. -1.  0.]
Bdot: [-1. -1.  0.]
[0.0146385  0.00327326 0.        ] [-0.32 -0.32  0

ValueError: setting an array element with a sequence.